In [4]:
!pip uninstall -y qiskit qiskit-terra qiskit-ibmq-provider
!pip install qiskit==0.42.1 qiskit-ibmq-provider==0.20.2

Found existing installation: qiskit 1.1.1
Uninstalling qiskit-1.1.1:
  Successfully uninstalled qiskit-1.1.1
Found existing installation: qiskit-terra 0.46.2
Uninstalling qiskit-terra-0.46.2:
  Successfully uninstalled qiskit-terra-0.46.2
Found existing installation: qiskit-ibmq-provider 0.20.2
Uninstalling qiskit-ibmq-provider-0.20.2:
  Successfully uninstalled qiskit-ibmq-provider-0.20.2
  Preparing metadata (setup.py) ... done
  Using cached qiskit_ibmq_provider-0.20.2-py3-none-any.whl (241 kB)
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.1/5.1 MB 5.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 12.8/12.8 MB 33.7 MB/s eta 0:00:00
  Created wheel for qiskit: filename=qiskit-0.42.1-py3-none-any.whl size=12920 sha256=41e68efd8040a22b8c448856ad709ffd7829a7313151123898be77229d6ab832
  Stored in directory: /root/.cache/pip/wheels/99/db/fa/cd33542aa8da5d5a2978cf2683dabf2ae67c732185a5cdb5a4
Successfully built qiskit


In [5]:
import sys
!{sys.executable} -m pip install --upgrade pip
!{sys.executable} -m pip install --upgrade qiskit==0.42.1 qiskit-ibmq-provider==0.20.2

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.8/1.8 MB 7.5 MB/s eta 0:00:00
  Attempting uninstall: pip
    Found existing installation: pip 23.1.2
    Uninstalling pip-23.1.2:
      Successfully uninstalled pip-23.1.2


In [9]:
from qiskit import QuantumCircuit, QuantumRegister, ClassicalRegister, execute, IBMQ
from qiskit.providers.ibmq import least_busy
from qiskit.tools.monitor import job_monitor
import getpass
import numpy as np
from statistics import mode

def create_circuit():
    qr = QuantumRegister(3, 'q')
    cr = ClassicalRegister(2, 'c')
    qc = QuantumCircuit(qr, cr)

    qc.h(qr[0])
    qc.cx(qr[0], qr[1])
    qc.s(qr[0])
    qc.cx(qr[1], qr[2])
    qc.h(qr[0])

    qc.measure(qr[0], cr[0])
    qc.measure(qr[2], cr[1])

    return qc

def simulate_and_analyze(backend, shots=1024):
    qc = create_circuit()
    job = execute(qc, backend, shots=shots)
    job_monitor(job)
    result = job.result().get_counts()

    prob_00 = result.get('00', 0) / shots
    prob_01 = result.get('01', 0) / shots

    return prob_00, prob_01

def interpret_result(prob_0_0, prob_0_1, threshold=0.15):
    diff = abs(prob_0_0 - prob_0_1)
    ratio = prob_0_0 / (prob_0_1 + 1e-10)  # Adăugăm o valoare mică pentru a evita împărțirea la zero

    if diff <= threshold and 0.8 < ratio < 1.2:
        return '1'
    elif prob_0_0 > 0.4:
        return '0'
    else:
        return '1'

def send_bit(bit, backend, repeats=3):
    results = []
    for _ in range(repeats):
        prob_0_0, prob_0_1 = simulate_and_analyze(backend)
        received = interpret_result(prob_0_0, prob_0_1)
        results.append(received == bit)
    return mode(results)  # Returnăm rezultatul majoritar

def send_message(message, backend):
    return [send_bit(bit, backend) for bit in message]

def receive_message(results):
    return ''.join('1' if result else '0' for result in results)

# Autentificare IBM Q
API_KEY = getpass.getpass('Introduceți cheia API IBM Q:')
IBMQ.save_account(API_KEY, overwrite=True)
IBMQ.load_account()

# Selectăm un backend IBM Q real
provider = IBMQ.get_provider(hub='ibm-q')
backend = least_busy(provider.backends(filters=lambda x: x.configuration().n_qubits >= 3 and
                                   not x.configuration().simulator and x.status().operational==True))
print(f"Vom folosi dispozitivul: {backend.name()}")

# Mesajul de 3 biți de transmis
message = "101"

print(f"Mesajul de transmis: {message}")

# Transmitem mesajul
sent_results = send_message(message, backend)
received_message = receive_message(sent_results)

print(f"\nMesaj trimis:    {message}")
print(f"Mesaj primit:    {received_message}")
print(f"Transmisie corectă: {message == received_message}")

print("\nDetalii pentru fiecare bit:")
for i, bit in enumerate(message):
    prob_0_0, prob_0_1 = simulate_and_analyze(backend)
    received = interpret_result(prob_0_0, prob_0_1)
    print(f"Bit {i}: Trimis {bit}, Primit {received}, "
          f"Prob(0,0): {prob_0_0:.4f}, Prob(0,1): {prob_0_1:.4f}, "
          f"Diferență: {abs(prob_0_0 - prob_0_1):.4f}, "
          f"Raport: {prob_0_0 / (prob_0_1 + 1e-10):.4f}")

Introduceți cheia API IBM Q:··········


ibmqfactory.load_account:WARNING:2024-06-30 04:54:24,055: Credentials are already in use. The existing account in the session will be replaced.


Vom folosi dispozitivul: ibm_kyoto
Mesajul de transmis: 101
Job Status: job has successfully run
Job Status: job has successfully run
Job Status: job has successfully run
Job Status: job has successfully run
Job Status: job has successfully run
Job Status: job has successfully run
Job Status: job has successfully run
Job Status: job has successfully run
Job Status: job has successfully run

Mesaj trimis:    101
Mesaj primit:    101
Transmisie corectă: True

Detalii pentru fiecare bit:
Job Status: job has successfully run
Bit 0: Trimis 1, Primit 1, Prob(0,0): 0.2754, Prob(0,1): 0.1943, Diferență: 0.0811, Raport: 1.4171
Job Status: job has successfully run
Bit 1: Trimis 0, Primit 1, Prob(0,0): 0.2705, Prob(0,1): 0.1787, Diferență: 0.0918, Raport: 1.5137
Job Status: job has successfully run
Bit 2: Trimis 1, Primit 1, Prob(0,0): 0.2969, Prob(0,1): 0.1787, Diferență: 0.1182, Raport: 1.6612
